In [1]:
import pandas as pd
import json
import os
import re 
# import pymupdf4llm
# import pymupdf
import sqlite3
import numpy as np

## Dataset: Training

In [2]:
# extract question and answer pairs from sql database medium variant

conn = sqlite3.connect("NewPipeChroma_Medium.db")

query = """
SELECT * from questions"""

df = pd.read_sql(query,conn)
print(len(df))
trainingdata = df[['question', 'answer']]
trainingdata['negative'] = np.random.permutation(trainingdata['answer'].values)
trainingdata = trainingdata.rename(columns={'question': 'anchor', 'answer': 'positive'})
trainingdata.head()

25485


C:\Users\victo\AppData\Local\Temp\ipykernel_24324\1157777622.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  trainingdata['negative'] = np.random.permutation(trainingdata['answer'].values)


anchor  \
0  Vraag 1\nHerinnert u zich dat de oud-Minister ...   
1  Vraag 2\nHerinnert u zich dat oud-Staatssecret...   
2  Vraag 3\nHerinnert u zich dat de op 20 maart 2...   
3  Vraag 4\nBent u ervan op de hoogte dat op het ...   
4  Vraag 5\nKunt u inzicht geven van elk van de b...   

                                            positive  \
0  Antwoord 1\nJa, ik verwijs hiertoe ook naar de...   
1  Antwoord 2\nJa. Staatssecretaris Snel heeft ge...   
2  Antwoord 3\nJa, ik ben bekend met deze uitspra...   
3  Antwoord 4\nJa. Zie ook mijn antwoord bij vraa...   
4  Antwoord 5\nTen aanzien van de bewindspersonen...   

                                            negative  
0  Antwoord 5 en 6\nSinds 2012 ondersteunt Nederl...  
1  Antwoord 6\nZie bijlage 1: Overzicht van wet- ...  
2  Antwoord 14\nJa. Tijdelijke flexwoningen kunne...  
3  Antwoord 10\nIn cao’s kunnen afspraken worden ...  
4  Antwoord 10\nIk verwijs hiervoor naar het antw...

In [3]:
trainingdata = trainingdata.replace(to_replace = r'^(?i)vraag(en)?(\s+\d+(,\s*\d+)*( en \d+)?)?(\n)?', value= '', regex=True)
trainingdata = trainingdata.replace(to_replace = r'^(?i)antwoord(en)?(\s+\d+(,\s*\d+)*( en \d+)?)?(\n)?', value= '', regex=True)

trainingdata.head()

anchor  \
0  Herinnert u zich dat de oud-Minister Kamp tijd...   
1  Herinnert u zich dat oud-Staatssecretaris Snel...   
2  Herinnert u zich dat de op 20 maart 2019 de Af...   
3  Bent u ervan op de hoogte dat op het blog van ...   
4  Kunt u inzicht geven van elk van de bewindsper...   

                                            positive  \
0  Ja, ik verwijs hiertoe ook naar de beantwoordi...   
1  Ja. Staatssecretaris Snel heeft geen medewerki...   
2  Ja, ik ben bekend met deze uitspraak van de Af...   
3             Ja. Zie ook mijn antwoord bij vraag 3.   
4  Ten aanzien van de bewindspersonen van het hui...   

                                            negative  
0  Sinds 2012 ondersteunt Nederland Suriname bij ...  
1  Zie bijlage 1: Overzicht van wet- en regelgeving.  
2  Ja. Tijdelijke flexwoningen kunnen een belangr...  
3  In cao’s kunnen afspraken worden gemaakt over ...  
4  Ik verwijs hiervoor naar het antwoord op vraag 3.

In [4]:
len(trainingdata)
# Check if lists have the same amount

25485

In [5]:
trainingdata.to_csv('finetuningdata_medium.csv')

In [6]:
df = pd.read_csv('./finetuningdata_medium.csv')
df.head()

Unnamed: 0                                             anchor  \
0           0  Herinnert u zich dat de oud-Minister Kamp tijd...   
1           1  Herinnert u zich dat oud-Staatssecretaris Snel...   
2           2  Herinnert u zich dat de op 20 maart 2019 de Af...   
3           3  Bent u ervan op de hoogte dat op het blog van ...   
4           4  Kunt u inzicht geven van elk van de bewindsper...   

                                            positive  \
0  Ja, ik verwijs hiertoe ook naar de beantwoordi...   
1  Ja. Staatssecretaris Snel heeft geen medewerki...   
2  Ja, ik ben bekend met deze uitspraak van de Af...   
3             Ja. Zie ook mijn antwoord bij vraag 3.   
4  Ten aanzien van de bewindspersonen van het hui...   

                                            negative  
0  Sinds 2012 ondersteunt Nederland Suriname bij ...  
1  Zie bijlage 1: Overzicht van wet- en regelgeving.  
2  Ja. Tijdelijke flexwoningen kunnen een belangr...  
3  In cao’s kunnen afspraken worden gemaakt over ...  
4  Ik verwijs hiervoor naar het antwoord op vraag 3.

In [7]:
df.replace(to_replace = r'\n', value= '', regex=True)
df.replace(to_replace = r'\[\d+\s\]', value= '', regex=True)
df = df.dropna() # Missing 40 missing postive negatives
df = df.astype(str)
df.head()

Unnamed: 0                                             anchor  \
0          0  Herinnert u zich dat de oud-Minister Kamp tijd...   
1          1  Herinnert u zich dat oud-Staatssecretaris Snel...   
2          2  Herinnert u zich dat de op 20 maart 2019 de Af...   
3          3  Bent u ervan op de hoogte dat op het blog van ...   
4          4  Kunt u inzicht geven van elk van de bewindsper...   

                                            positive  \
0  Ja, ik verwijs hiertoe ook naar de beantwoordi...   
1  Ja. Staatssecretaris Snel heeft geen medewerki...   
2  Ja, ik ben bekend met deze uitspraak van de Af...   
3             Ja. Zie ook mijn antwoord bij vraag 3.   
4  Ten aanzien van de bewindspersonen van het hui...   

                                            negative  
0  Sinds 2012 ondersteunt Nederland Suriname bij ...  
1  Zie bijlage 1: Overzicht van wet- en regelgeving.  
2  Ja. Tijdelijke flexwoningen kunnen een belangr...  
3  In cao’s kunnen afspraken worden gemaakt over ...  
4  Ik verwijs hiervoor naar het antwoord op vraag 3.

In [8]:
# Split sets
# Traning/Test/Validation
# 80/20/10

from sklearn.model_selection import train_test_split

train, test = train_test_split(df, test_size=0.2)

train, validation = train_test_split(train, test_size=0.1)
print(train.columns)

train = train.fillna(value="")
test= test.fillna(value="")
validation=validation.fillna(value="")

train.to_csv('../datasets/train.csv')
test.to_csv('../datasets/test.csv')
validation.to_csv('../datasets/validation.csv')
print(f"trainset len {len(train)}")
print(f"Testset len {len(test)}")
print(f"validationset len {len(validation)}")

Index(['Unnamed: 0', 'anchor', 'positive', 'negative'], dtype='object')
trainset len 18291
Testset len 5081
validationset len 2033


In [9]:
# train = train.to_dict(orient="records")
# validation = validation.to_dict(orient="records")
# test = test.to_dict(orient="records")


In [10]:
print(train)

      Unnamed: 0                                             anchor  \
378          378  Kunt u verklaren met welke redenen Nederland m...   
10764      10764  Indien deze maatregel genomen wordt, is er dan...   
14682      14682  In hoeverre en op welke wijze zet u zich in om...   
1656        1656  Welke consequenties zijn er voor Nederlanders ...   
1983        1983  Wat moet er gebeuren voordat de mensen van Sin...   
...          ...                                                ...   
16956      16956  Zijn er op dit moment nog andere veroordeelde ...   
15231      15231  Op welke termijn worden welke stappen gezet om...   
8012        8012  Bent u op de hoogte van het advies van de Raad...   
2622        2622  Welke risico’s ziet u voor het welzijn van die...   
7041        7041  Waarom zaten er in de DOBC ook leden van het O...   

                                                positive  \
378    Toen Nederland na de genocide van 1994 begon m...   
10764  Het besluitvormingsp

In [11]:
from sentence_transformers import SentenceTransformer
from sentence_transformers.losses import CachedMultipleNegativesRankingLoss



c:\Users\victo\AppData\Local\Programs\Python\Python310\lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [12]:
# source: https://huggingface.co/blog/train-sentence-transformers by Tom Aarsen

from torch.utils.data import DataLoader
from datasets import load_dataset
from sentence_transformers import (SentenceTransformer, 
    SentenceTransformerTrainer,
    SentenceTransformerTrainingArguments,
    SentenceTransformerModelCardData, SimilarityFunction
)
from sentence_transformers.losses import CachedMultipleNegativesRankingLoss
from sentence_transformers import LoggingHandler
from sentence_transformers.evaluation import TripletEvaluator
from sentence_transformers.training_args import BatchSamplers
import wandb

run = wandb.init(project = "finetune-embeddings_1")

# 1. Load a model to finetune with 2. (Optional) model card data
model = SentenceTransformer(
    "textgain/allnli-GroNLP-bert-base-dutch-cased",
    model_card_data=SentenceTransformerModelCardData(
        language="Dutch",
        license="",
        model_name="textgain/allnli-GroNLP-bert-base-dutch-cased_finetuned_on_Kamervragentest",
    )
)
# 3. Load a dataset to finetune on
# dataset = load_dataset("sentence-transformers/all-nli", "triplet")

data_files = {
    "train": "C:\\Users\\victo\\LearningLion-Finetune\\LearningLion-FineTuneEmbeddings\\datasets\\train.csv",
    "test": "C:\\Users\\victo\\LearningLion-Finetune\\LearningLion-FineTuneEmbeddings\\datasets\\test.csv",
    "eval": "C:\\Users\\victo\\LearningLion-Finetune\\LearningLion-FineTuneEmbeddings\\datasets\\validation.csv"
}
datasets = load_dataset('csv', data_files=data_files)

wandb: Using wandb-core as the SDK backend.  Please refer to https://wandb.me/wandb-core for more information.
wandb: Currently logged in as: mark. Use `wandb login --relogin` to force relogin


Generating train split: 18291 examples [00:00, 84751.34 examples/s]
Generating test split: 5081 examples [00:00, 82933.83 examples/s]
Generating eval split: 2033 examples [00:00, 78403.61 examples/s]


In [13]:
print(datasets['train']['anchor'])

['Kunt u verklaren met welke redenen Nederland met bijna 140 miljoen euro\ndictatoriaal Rwanda heeft gefinancierd?', 'Indien deze maatregel genomen wordt, is er dan gelekt uit vertrouwelijke\nstukken van het kabinet?', 'In hoeverre en op welke wijze zet u zich in om ervoor te zorgen dat de\nOegandese autoriteiten de aanbevelingen van voorgaande internationale\nobservatiemissies alsnog aanneemt en implementeert?', 'Welke consequenties zijn er voor Nederlanders die Oekraïners opvangen,\nmaar die zelf ondersteuning ontvangen, zoals WMO-voorzieningen? Is het de\nbedoeling dat gemeenten inwoners die opvang bieden hierop korten, of geldt\nhiervoor hetzelfde als voor de kostendelersnorm, dat mensen er niet op\nachteruit mogen gaan? Zo ja, kunt u gemeenten hierover informeren?', 'Wat moet er gebeuren voordat de mensen van Sint Maarten, die nog altijd in\nvervallen en verwoeste woningen wonen, eindelijk geholpen worden?', 'Zijn er meer projecten of opdrachten gegund aan stichtingen, bedrijven o

In [14]:
print(datasets.column_names)

{'train': ['Unnamed: 0.1', 'Unnamed: 0', 'anchor', 'positive', 'negative'], 'test': ['Unnamed: 0.1', 'Unnamed: 0', 'anchor', 'positive', 'negative'], 'eval': ['Unnamed: 0.1', 'Unnamed: 0', 'anchor', 'positive', 'negative']}


In [15]:
# 6. (Optional) Create an evaluator & evaluate the base model

anchor_eval = datasets['eval']["anchor"]#.to_list()
positive_eval = datasets['eval']["positive"]#.to_list()
negative_eval = datasets['eval']["negative"]#.to_list()
anchor_test = datasets["test"]["anchor"]
positive_test = datasets["test"]["positive"]
negative_test = datasets["test"]["negative"]

In [16]:
# 6. (Optional) Create an evaluator & evaluate the base model
dev_evaluator = TripletEvaluator(
    anchors=anchor_eval,
    positives=positive_eval,
    negatives=negative_eval,
    main_distance_function =SimilarityFunction.COSINE, 
    name="tripleteval",
    show_progress_bar=True
)

test_evaluator = TripletEvaluator(
    anchors=anchor_test,
    positives=positive_test,
    negatives=negative_test,
    main_distance_function =SimilarityFunction.COSINE, 
    name="tripleteval",
    show_progress_bar=True
)


print(model)
dev_evaluator(model)
validation_eval = dev_evaluator(model)
wandb.log({"OG_loss_validation": validation_eval})
test_eval = test_evaluator(model)
wandb.log({"OG_loss_test": test_eval})

SentenceTransformer(
  (0): Transformer({'max_seq_length': 75, 'do_lower_case': False}) with Transformer model: BertModel 
  (1): Pooling({'word_embedding_dimension': 768, 'pooling_mode_cls_token': False, 'pooling_mode_mean_tokens': True, 'pooling_mode_max_tokens': False, 'pooling_mode_mean_sqrt_len_tokens': False, 'pooling_mode_weightedmean_tokens': False, 'pooling_mode_lasttoken': False, 'include_prompt': True})
)


Batches:   0%|          | 0/128 [00:00<?, ?it/s]c:\Users\victo\AppData\Local\Programs\Python\Python310\lib\site-packages\transformers\models\bert\modeling_bert.py:440: UserWarning: 1Torch was not compiled with flash attention. (Triggered internally at C:\actions-runner\_work\pytorch\pytorch\builder\windows\pytorch\aten\src\ATen\native\transformers\cuda\sdp_utils.cpp:555.)
  attn_output = torch.nn.functional.scaled_dot_product_attention(
Batches: 100%|██████████| 318/318 [00:04<00:00, 67.17it/s] 


In [17]:
# 4. Define a loss function
loss = CachedMultipleNegativesRankingLoss(model)

# 5. (Optional) Specify training arguments
args = SentenceTransformerTrainingArguments(
    # Required parameter:
    output_dir="./",
    # Optional training parameters:
    num_train_epochs=4,
    per_device_train_batch_size=64,
    per_device_eval_batch_size=64,
    warmup_ratio=0.1,
    fp16=True,  # Set to False if GPU can't handle FP16
    bf16=False,  # Set to True if GPU supports BF16
    batch_sampler=BatchSamplers.NO_DUPLICATES,  # MultipleNegativesRankingLoss benefits from no duplicates
    # Optional tracking/debugging parameters:
    logging_dir="../logs",  # Directory for logs
    logging_steps=10,      # Log every 10 steps
    save_strategy="steps", # Save the model after each epoch
    eval_strategy="steps", # Evaluate after each epoch,
    report_to='wandb',
    eval_steps=10,
    save_steps=10,
    save_total_limit=2,
    run_name="fiddlingaround",
    load_best_model_at_end=True,
)
print(args)
args =args.set_logging(strategy="steps",report_to=["wandb"])
print(args)

SentenceTransformerTrainingArguments(
_n_gpu=1,
accelerator_config={'split_batches': False, 'dispatch_batches': None, 'even_batches': True, 'use_seedable_sampler': True, 'non_blocking': False, 'gradient_accumulation_kwargs': None, 'use_configured_state': False},
adafactor=False,
adam_beta1=0.9,
adam_beta2=0.999,
adam_epsilon=1e-08,
auto_find_batch_size=False,
batch_eval_metrics=False,
batch_sampler=no_duplicates,
bf16=False,
bf16_full_eval=False,
data_seed=None,
dataloader_drop_last=False,
dataloader_num_workers=0,
dataloader_persistent_workers=False,
dataloader_pin_memory=True,
dataloader_prefetch_factor=None,
ddp_backend=None,
ddp_broadcast_buffers=False,
ddp_bucket_cap_mb=None,
ddp_find_unused_parameters=None,
ddp_timeout=1800,
debug=[],
deepspeed=None,
disable_tqdm=False,
dispatch_batches=None,
do_eval=True,
do_predict=False,
do_train=False,
eval_accumulation_steps=None,
eval_delay=0,
eval_do_concat_batches=True,
eval_on_start=False,
eval_steps=10,
eval_strategy=steps,
eval_use_gat

# trainer

In [18]:
trainer = SentenceTransformerTrainer(
    model=model,
    args=args,
    train_dataset=datasets['train'].select_columns(["anchor", "positive", "negative"]),
    eval_dataset=datasets['eval'].select_columns(["anchor", "positive", "negative"]),
    loss=loss,
    evaluator= dev_evaluator
          #wandb.log({'evalscore': evaluation_score[dev_evaluator.primary_metric]})
    #show_progress_bar=True

)

trainer.train()


  1%|          | 10/1144 [00:04<07:04,  2.67it/s]












Batches: 100%|██████████| 128/128 [00:01<00:00, 96.00it/s] 













Batches: 100%|██████████| 128/128 [00:01<00:00, 94.81it/s] 













Batches: 100%|██████████| 128/128 [00:01<00:00, 92.73it/s]
                                                 
  1%|          | 10/1144 [00:19<07:04,  2.67it/s]

{'eval_loss': 1.0968053340911865, 'eval_tripleteval_cosine_accuracy': 0.8912936546974914, 'eval_runtime': 15.789, 'eval_samples_per_second': 128.761, 'eval_steps_per_second': 2.027, 'epoch': 0.03}


  2%|▏         | 20/1144 [00:24<10:48,  1.73it/s]  












Batches: 100%|██████████| 128/128 [00:01<00:00, 95.94it/s]













Batches: 100%|██████████| 128/128 [00:01<00:00, 95.67it/s] 














Batches: 100%|██████████| 128/128 [00:01<00:00, 93.55it/s] 
                                                 
  2%|▏         | 20/1144 [00:40<10:48,  1.73it/s]

{'eval_loss': 0.6039100885391235, 'eval_tripleteval_cosine_accuracy': 0.9247417609444171, 'eval_runtime': 15.6587, 'eval_samples_per_second': 129.832, 'eval_steps_per_second': 2.044, 'epoch': 0.07}


  3%|▎         | 30/1144 [00:45<10:53,  1.70it/s]  












Batches: 100%|██████████| 128/128 [00:01<00:00, 97.44it/s] 













Batches: 100%|██████████| 128/128 [00:01<00:00, 93.89it/s]














Batches: 100%|██████████| 128/128 [00:01<00:00, 90.64it/s]
                                                 
  3%|▎         | 30/1144 [01:00<10:53,  1.70it/s]

...

100%|█████████▉| 1140/1144 [40:46<00:01,  2.46it/s]

















Batches: 100%|██████████| 128/128 [00:01<00:00, 67.72it/s]


















Batches: 100%|██████████| 128/128 [00:01<00:00, 65.08it/s]


















Batches: 100%|██████████| 128/128 [00:01<00:00, 64.49it/s]
                                                   
100%|█████████▉| 1140/1144 [41:04<00:01,  2.46it/s]

{'eval_loss': 0.3011758625507355, 'eval_tripleteval_cosine_accuracy': 0.9640924741760944, 'eval_runtime': 18.5157, 'eval_samples_per_second': 109.799, 'eval_steps_per_second': 1.728, 'epoch': 3.99}


100%|██████████| 1144/1144 [41:07<00:00,  2.16s/it]

{'train_runtime': 2467.8663, 'train_samples_per_second': 29.647, 'train_steps_per_second': 0.464, 'train_loss': 0.487558301512178, 'epoch': 4.0}


TrainOutput(global_step=1144, training_loss=0.487558301512178, metrics={'train_runtime': 2467.8663, 'train_samples_per_second': 29.647, 'train_steps_per_second': 0.464, 'total_flos': 0.0, 'train_loss': 0.487558301512178, 'epoch': 4.0})

In [19]:

# (Optional) Evaluate the trained model on the test set, after training completes

# test_evaluator = TripletEvaluator(
#     anchors=anchor_test,
#     positives=positive_test,
#     negatives=negative_test,
#     main_distance_function = SimilarityFunction.COSINE,
#     name="aftertrained",
#     show_progress_bar=True
# )
# test_evaluator(model)

# 8. Save the trained model
model.save_pretrained(r"C:\Users\victo\LearningLion-Finetune\LearningLion-FineTuneEmbeddings\models")



print(model)
dev_evaluator(model)
validation_eval = dev_evaluator(model)
wandb.log({"TRAINED_loss_validation": validation_eval})
test_eval = test_evaluator(model)
wandb.log({"TRAINED_loss_test": test_eval})


wandb.finish()


SentenceTransformer(
  (0): Transformer({'max_seq_length': 75, 'do_lower_case': False}) with Transformer model: BertModel 
  (1): Pooling({'word_embedding_dimension': 768, 'pooling_mode_cls_token': False, 'pooling_mode_mean_tokens': True, 'pooling_mode_max_tokens': False, 'pooling_mode_mean_sqrt_len_tokens': False, 'pooling_mode_weightedmean_tokens': False, 'pooling_mode_lasttoken': False, 'include_prompt': True})
)


Batches: 100%|██████████| 318/318 [00:02<00:00, 109.39it/s]
